In [26]:
# Render our plots inline
%matplotlib inline

import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from ta.trend import ADXIndicator

# Make the graphs a bit prettier, and bigger
plt.style.use('ggplot')
plt.rcParams['figure.figsize'] = (15, 5)

# Panda plot sample
# https://pandas.pydata.org/pandas-docs/version/0.13/visualization.html

# 1 Process the raw stock trading history csv file
## 1.1 Load dataframe and combine data from past

In [27]:
df_hourly_21_03_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_hour_3months_combined_21_03_2021.csv", sep=",", index_col='begins_at')
df_hourly_21_03_2021.index.astype('datetime64[ns]')

df_hourly_28_03_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_hour_3months_combined_28_03_2021.csv", sep=",", index_col='begins_at')
df_hourly_28_03_2021.index.astype('datetime64[ns]')

df_5min_21_03_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_5min_weekly_combined_21_03_2021.csv", sep=",", index_col='begins_at')
df_5min_21_03_2021.index.astype('datetime64[ns]')

df_5min_28_03_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_5min_weekly_combined_28_03_2021.csv", sep=",", index_col='begins_at')
df_5min_28_03_2021.index.astype('datetime64[ns]')

df_5min_31_03_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_5min_weekly_combined_31_03_2021.csv", sep=",", index_col='begins_at')
df_5min_31_03_2021.index.astype('datetime64[ns]')

df_5min_08_04_2021 = pd.read_csv("../data/btc_gbtc/btc_gbtc_5min_weekly_combined_08_04_2021.csv", sep=",", index_col='begins_at')
df_5min_08_04_2021.index.astype('datetime64[ns]')

df_min_td = pd.read_csv("../data/btc_gbtc/btc_gbtc_minute_2021.csv", sep=",", index_col='begins_at')
df_min_td.drop(df_min_td[df_min_td['open_price_y'].isnull()].index, inplace=True)
df_min_td.index.astype('datetime64[ns]')

df_hourly = pd.concat([df_hourly_21_03_2021, df_hourly_28_03_2021]).drop_duplicates().sort_index(ascending=True)
df_5min = pd.concat([df_5min_31_03_2021, df_5min_08_04_2021]).drop_duplicates().sort_index(ascending=True)

# df_5min
df_min_td[:3]
# _x is btc price, _y is gbtc price, btc trades with 24x7 but gbtc only trades when stock market open.

low_price_x  high_price_x  close_price_x  open_price_x  \
begins_at                                                                     
2021-03-03 13:00:00     52400.00      52666.00       52419.63      52593.84   
2021-03-03 13:01:00     52387.00      52493.08       52457.70      52409.20   
2021-03-03 13:02:00     52444.78      52499.00       52476.95      52460.38   

                      volume_x        time  open_price_y  high_price_y  \
begins_at                                                                
2021-03-03 13:00:00  53.035290  1614776400         48.53        49.700   
2021-03-03 13:01:00  18.432343  1614776460         49.00        49.380   
2021-03-03 13:02:00  12.044772  1614776520         49.00        49.175   

                     low_price_y  close_price_y  volume_y  
begins_at                                                  
2021-03-03 13:00:00        48.53           49.0   27987.0  
2021-03-03 13:01:00        48.69           49.0    3445.0  
2021-03-03 13:02:00        48.69           48.9     424.0

## 1.2 Add calculation NAV column and rename columns

In [28]:
# add btc nav per share column (bitcoin per share fluctuates, so use average here)
btc_per_share = (0.00094607 + 0.00094509) / 2 


df_hourly = df_hourly.rename(columns={"open_price_y": "gbtc_open_price", "close_price_y": "gbtc_close_price", "high_price_y": "gbtc_high_price", "low_price_y": "gbtc_low_price", "volume_y": "gbtc_volume"})
df_hourly["nav_open_price"] = df_hourly["open_price_x"] * btc_per_share
df_hourly["nav_close_price"] = df_hourly["close_price_x"] * btc_per_share
df_hourly["nav_high_price"] = df_hourly["high_price_x"] * btc_per_share
df_hourly["nav_low_price"] = df_hourly["low_price_x"] * btc_per_share

df_5min = df_5min.rename(columns={"open_price_y": "gbtc_open_price", "close_price_y": "gbtc_close_price", "high_price_y": "gbtc_high_price", "low_price_y": "gbtc_low_price", "volume_y": "gbtc_volume"})
df_5min["nav_open_price"] = df_5min["open_price_x"] * btc_per_share
df_5min["nav_close_price"] = df_5min["close_price_x"] * btc_per_share
df_5min["nav_high_price"] = df_5min["high_price_x"] * btc_per_share
df_5min["nav_low_price"] = df_5min["low_price_x"] * btc_per_share

df_min_td = df_min_td.rename(columns={"open_price_y": "gbtc_open_price", "close_price_y": "gbtc_close_price", "high_price_y": "gbtc_high_price", "low_price_y": "gbtc_low_price", "volume_y": "gbtc_volume"})
df_min_td["nav_open_price"] = df_min_td["open_price_x"] * btc_per_share
df_min_td["nav_close_price"] = df_min_td["close_price_x"] * btc_per_share
df_min_td["nav_high_price"] = df_min_td["high_price_x"] * btc_per_share
df_min_td["nav_low_price"] = df_min_td["low_price_x"] * btc_per_share

df_min_td

low_price_x  high_price_x  close_price_x  open_price_x  \
begins_at                                                                     
2021-03-03 13:00:00     52400.00      52666.00       52419.63      52593.84   
2021-03-03 13:01:00     52387.00      52493.08       52457.70      52409.20   
2021-03-03 13:02:00     52444.78      52499.00       52476.95      52460.38   
2021-03-03 13:03:00     52429.72      52507.91       52455.91      52476.94   
2021-03-03 13:04:00     52376.32      52471.99       52468.75      52462.57   
...                          ...           ...            ...           ...   
2021-04-16 20:00:00     61852.74      61939.99       61876.72      61852.74   
2021-04-16 20:01:00     61825.25      61896.74       61875.11      61879.42   
2021-04-16 20:07:00     61872.04      61940.00       61939.99      61872.05   
2021-04-16 20:08:00     61888.82      61949.21       61888.83      61939.99   
2021-04-16 20:09:00     61888.82      61917.74       61916.68      61888.83   

                      volume_x        time  gbtc_open_price  gbtc_high_price  \
begins_at                                                                      
2021-03-03 13:00:00  53.035290  1614776400            48.53           49.700   
2021-03-03 13:01:00  18.432343  1614776460            49.00           49.380   
2021-03-03 13:02:00  12.044772  1614776520            49.00           49.175   
2021-03-03 13:03:00  22.257132  1614776580            48.90           49.200   
2021-03-03 13:04:00  27.589103  1614776640            49.11           49.200   
...                        ...         ...              ...              ...   
2021-04-16 20:00:00  33.847123  1618603200            51.38           51.380   
2021-04-16 20:01:00  14.174098  1618603260            51.39           51.390   
2021-04-16 20:07:00   4.571577  1618603620            51.39           51.390   
2021-04-16 20:08:00   5.670370  1618603680            51.39           51.390   
2021-04-16 20:09:00   3.144391  1618603740            51.39           51.390   

                     gbtc_low_price  gbtc_close_price  gbtc_volume  \
begins_at                                                            
2021-03-03 13:00:00           48.53             49.00      27987.0   
2021-03-03 13:01:00           48.69             49.00       3445.0   
2021-03-03 13:02:00           48.69             48.90        424.0   
2021-03-03 13:03:00           48.81             49.20        621.0   
2021-03-03 13:04:00           49.00             49.18       5106.0   
...                             ...               ...          ...   
2021-04-16 20:00:00           51.37             51.37       7113.0   
2021-04-16 20:01:00           51.39             51.39        100.0   
2021-04-16 20:07:00           51.39             51.39       2500.0   
2021-04-16 20:08:00           51.39             51.39       3500.0   
2021-04-16 20:09:00           51.39             51.39        329.0   

                     nav_open_price  nav_close_price  nav_high_price  \
begins_at                                                              
2021-03-03 13:00:00       49.731683        49.566954       49.799916   
2021-03-03 13:01:00       49.557091        49.602952       49.636407   
2021-03-03 13:02:00       49.605486        49.621154       49.642004   
2021-03-03 13:03:00       49.621145        49.601259       49.650430   
2021-03-03 13:04:00       49.607557        49.613401       49.616464   
...                             ...              ...             ...   
2021-04-16 20:00:00       58.486714        58.509389       58.569216   
2021-04-16 20:01:00       58.511942        58.507867       58.528319   
2021-04-16 20:07:00       58.504973        58.569216       58.569225   
2021-04-16 20:08:00       58.569216        58.520840       58.577934   
2021-04-16 20:09:00       58.520840        58.547174       58.548177   

                     nav_low_price  
begins_at                           
2021-03-03 13:00:00      49.54

# 2. Graph analysis

## 2.1 Hourly graph

In [29]:
import plotly.graph_objects as go
pd.options.plotting.backend = "plotly"


In [30]:
# btc hourly price history graph (2020-12 / 2021-3)
df_hourly["nav_open_price"].plot()

# TODO: show max diff and percentage in each hour between high and low

fig = df_hourly.loc[:,["nav_open_price", "nav_high_price", "nav_low_price"]].plot.line()
fig.update_layout(
    autosize=False,
    width=5000,
    height=600,
    paper_bgcolor="LightSteelBlue",
)

fig.update_xaxes(nticks=300)          
fig.show()

In [31]:
# hourly chart comparison
import matplotlib.dates as mdates
import matplotlib as plt

fig = df_hourly.loc[:,["nav_open_price", "nav_high_price", "nav_low_price", "gbtc_open_price", "gbtc_high_price", "gbtc_low_price"]].plot.line()
fig.update_layout(
    autosize=False,
    width=5000,
    height=600,
    paper_bgcolor="LightSteelBlue",
)

fig.update_xaxes(nticks=300)          
fig.show()

In [32]:
## 2.2 5 Minute chart analysis

In [36]:
df_min_td["premium_high"] = (df_min_td["gbtc_high_price"] - df_min_td["nav_high_price"]) / df_min_td["nav_high_price"]
df_min_td["premium_high"].dropna()
df_min_td["premium_low"] = (df_min_td["gbtc_low_price"] - df_min_td["nav_low_price"]) / df_min_td["nav_low_price"]
df_min_td["premium_low"].dropna()
df_min_td["premium_close"] = (df_min_td["gbtc_close_price"] - df_min_td["nav_close_price"]) / df_min_td["nav_close_price"]
df_min_td["premium_close"].dropna()

# Calculate ADX
adxI = ADXIndicator(df_min_td['premium_high'], df_min_td['premium_low'], df_min_td['premium_close'], 14, False)
df_min_td['pos_directional_indicator'] = adxI.adx_pos()
df_min_td['neg_directional_indicator'] = adxI.adx_neg()
df_min_td['adx'] = adxI.adx() 

df_min_td[:4]

/usr/local/lib/python3.9/site-packages/ta/trend.py:768: RuntimeWarning:

invalid value encountered in double_scalars

/usr/local/lib/python3.9/site-packages/ta/trend.py:772: RuntimeWarning:

invalid value encountered in double_scalars



low_price_x  high_price_x  close_price_x  open_price_x  \
begins_at                                                                     
2021-03-03 13:00:00     52400.00      52666.00       52419.63      52593.84   
2021-03-03 13:01:00     52387.00      52493.08       52457.70      52409.20   
2021-03-03 13:02:00     52444.78      52499.00       52476.95      52460.38   
2021-03-03 13:03:00     52429.72      52507.91       52455.91      52476.94   

                      volume_x        time  gbtc_open_price  gbtc_high_price  \
begins_at                                                                      
2021-03-03 13:00:00  53.035290  1614776400            48.53           49.700   
2021-03-03 13:01:00  18.432343  1614776460            49.00           49.380   
2021-03-03 13:02:00  12.044772  1614776520            49.00           49.175   
2021-03-03 13:03:00  22.257132  1614776580            48.90           49.200   

                     gbtc_low_price  gbtc_close_price  ...  nav_open_price  \
begins_at                                              ...                   
2021-03-03 13:00:00           48.53              49.0  ...       49.731683   
2021-03-03 13:01:00           48.69              49.0  ...       49.557091   
2021-03-03 13:02:00           48.69              48.9  ...       49.605486   
2021-03-03 13:03:00           48.81              49.2  ...       49.621145   

                     nav_close_price  nav_high_price  nav_low_price  \
begins_at                                                             
2021-03-03 13:00:00        49.566954       49.799916      49.548392   
2021-03-03 13:01:00        49.602952       49.636407      49.536099   
2021-03-03 13:02:00        49.621154       49.642004      49.590735   
2021-03-03 13:03:00        49.601259       49.650430      49.576495   

                     premium_high  premium_low  premium_close  \
begins_at                                                       
2021-03-03 13:00:00     -0.002006    -0.020553      -0.011438   
2021-03-03 13:01:00     -0.005166    -0.017080      -0.012156   
2021-03-03 13:02:00     -0.009407    -0.018163      -0.014533   
2021-03-03 13:03:00     -0.009072    -0.015461      -0.008090   

                     pos_directional_indicator  neg_directional_indicator  adx  
begins_at                                                                       
2021-03-03 13:00:00                        0.0                        0.0  0.0  
2021-03-03 13:01:00                        0.0                        0.0  0.0  
2021-03-03 13:02:00                        0.0                        0.0  0.0  
2021-03-03 13:03:00                        0.0                        0.0  0.0  

[4 rows x 21 columns]

In [15]:
## 2.2 5 5-Minute chart analysis

In [25]:
df_5min.shape

(3147, 20)

In [34]:
df_5min["premium_high"] = (df_5min["gbtc_high_price"] - df_5min["nav_high_price"]) / df_5min["nav_high_price"]
df_5min["premium_high"].dropna()
df_5min["premium_low"] = (df_5min["gbtc_low_price"] - df_5min["nav_low_price"]) / df_5min["nav_low_price"]
df_5min["premium_low"].dropna()
df_5min["premium_close"] = (df_5min["gbtc_close_price"] - df_5min["nav_close_price"]) / df_5min["nav_close_price"]
df_5min["premium_close"].dropna()

# Calculate ADX
adxI = ADXIndicator(df_5min['premium_high'], df_5min['premium_low'], df_5min['premium_close'], 14, False)
df_5min['pos_directional_indicator'] = adxI.adx_pos()
df_5min['neg_directional_indicator'] = adxI.adx_neg()
df_5min['adx'] = adxI.adx() 

df_5min[:4]

/usr/local/lib/python3.9/site-packages/ta/trend.py:768: RuntimeWarning:

invalid value encountered in double_scalars

/usr/local/lib/python3.9/site-packages/ta/trend.py:772: RuntimeWarning:

invalid value encountered in double_scalars



open_price_x  close_price_x  high_price_x   low_price_x  \
begins_at                                                                       
2021-03-24T14:50:00Z     56692.525      56852.575     56929.040  56425.135000   
2021-03-24T14:55:00Z     56852.575      56439.065     56903.795  56280.220000   
2021-03-24T15:00:00Z     56439.065      56650.185     56809.080  56319.400000   
2021-03-24T15:05:00Z     56650.185      56526.490     56813.520  56253.151137   

                      volume_x session_x  interpolated_x symbol_x  \
begins_at                                                           
2021-03-24T14:50:00Z         0       reg           False   BTCUSD   
2021-03-24T14:55:00Z         0       reg           False   BTCUSD   
2021-03-24T15:00:00Z         0       reg           False   BTCUSD   
2021-03-24T15:05:00Z         0       reg           False   BTCUSD   

                      gbtc_open_price  gbtc_close_price  ...  nav_open_price  \
begins_at                                                ...                   
2021-03-24T14:50:00Z              NaN               NaN  ...       53.607318   
2021-03-24T14:55:00Z              NaN               NaN  ...       53.758658   
2021-03-24T15:00:00Z              NaN               NaN  ...       53.367651   
2021-03-24T15:05:00Z              NaN               NaN  ...       53.567282   

                      nav_close_price  nav_high_price nav_low_price  \
begins_at                                                             
2021-03-24T14:50:00Z        53.758658       53.830962     53.354479   
2021-03-24T14:55:00Z        53.367651       53.807090     53.217450   
2021-03-24T15:00:00Z        53.567282       53.717530     53.254498   
2021-03-24T15:05:00Z        53.450318       53.721728     53.191855   

                     premium_high premium_low  premium_close  \
begins_at                                                      
2021-03-24T14:50:00Z          NaN         NaN            NaN   
2021-03-24T14:55:00Z          NaN         NaN            NaN   
2021-03-24T15:00:00Z          NaN         NaN            NaN   
2021-03-24T15:05:00Z          NaN         NaN            NaN   

                      pos_directional_indicator  neg_directional_indicator  \
begins_at                                                                    
2021-03-24T14:50:00Z                        0.0                        0.0   
2021-03-24T14:55:00Z                        0.0                        0.0   
2021-03-24T15:00:00Z                        0.0                        0.0   
2021-03-24T15:05:00Z                        0.0                        0.0   

                      adx  
begins_at                  
2021-03-24T14:50:00Z  0.0  
2021-03-24T14:55:00Z  0.0  
2021-03-24T15:00:00Z  0.0  
2021-03-24T15:05:00Z  0.0  

[4 rows x 26 columns]

In [37]:
# Try use plotly for interactive graph

price_src = df_min_td.loc[:,['nav_open_price','gbtc_open_price']]

fig = price_src.plot.line()
fig.update_layout(
    autosize=False,
    width=5000,
    height=800,
    paper_bgcolor="LightSteelBlue",
)

fig.update_xaxes(nticks=200)          
fig.show()

In [30]:
# Thoughts
# Check premium, low premium (ex: -5%) could be buying areas, high premium (+/- 1%) could be selling areas. 
#  Need to verify the expected number. 
# The thoughts is, arbitrage suppose to buy when the premium is low while retail buyer is selling.  arbitrage suppose to sell when retail buyer wants to buy. 
# So we could use premium change rates as an reverse indicator to decide to buy or sell0

In [31]:
df_5min.index

Index(['2021-03-15T00:50:00Z', '2021-03-15T00:55:00Z', '2021-03-15T01:00:00Z',
       '2021-03-15T01:05:00Z', '2021-03-15T01:10:00Z', '2021-03-15T01:15:00Z',
       '2021-03-15T01:20:00Z', '2021-03-15T01:25:00Z', '2021-03-15T01:30:00Z',
       '2021-03-15T01:35:00Z',
       ...
       '2021-04-08T21:25:00Z', '2021-04-08T21:30:00Z', '2021-04-08T21:35:00Z',
       '2021-04-08T21:40:00Z', '2021-04-08T21:45:00Z', '2021-04-08T21:50:00Z',
       '2021-04-08T21:55:00Z', '2021-04-08T22:00:00Z', '2021-04-08T22:05:00Z',
       '2021-04-08T22:10:00Z'],
      dtype='object', name='begins_at', length=6868)

In [38]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def plot_price_chart(df, chart_width=5000, chart_height=800, nticks=200):
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.add_trace(go.Scatter(x=df.index, y=df["nav_close_price"], mode='lines+markers', name="btc nav close price"), secondary_y=False)
    fig.add_trace(go.Scatter(x=df.index, y=df["gbtc_close_price"], mode='lines+markers', name="gbtc clsoe price"), secondary_y=False)
    fig.add_trace(go.Scatter(x=df.index, y=df["premium_close"], mode='lines+markers', name="gbtc premium close percentage"), secondary_y=True)
    fig.add_trace(go.Scatter(x=df.index, y=df["adx"], mode='lines+markers', name="adx percentage"), secondary_y=True)

    fig.update_layout(
        autosize=False,
        width=5000,
        height=800,
        paper_bgcolor="LightSteelBlue",
    )

    fig.update_yaxes(title_text="price", secondary_y=False)
    fig.update_yaxes(title_text="premium to gbtc price percentage", secondary_y=True)

    fig.update_xaxes(nticks=200)          
    fig.show()

In [39]:

# Plot the full time range, include stock market close date

plot_price_chart(df_min_td)